In [2]:
#Import necessary modules
import impact as                             impt
import impact.plotting as                    implot
from impact.parsers import Parser as parser
import numpy as np
#SETTINGS FOR IMPACT. Change settings to alter calculations as required
impt.settings.perform_curve_fit = False
impt.settings.fit_type = 'gompertz'
impt.settings.outlier_cleaning_flag = True
impt.settings.max_fraction_replicates_to_remove = 0.3
impt.settings.std_deviation_cutoff=0.1
impt.settings.verbose = False
impt.settings.live_calculations = False
impt.settings.use_filtered_data = False
impt.settings.death_phase_hyperparameter = 1

import sys
if 'ipykernel' in sys.modules:
    from plotly.offline import init_notebook_mode
    from plotly.offline import iplot as plot
    from IPython.display import HTML

    # This is required for correct mathjax (latex) and documentation rendering
    HTML(
        """
        <script>
            var waitForPlotly = setInterval( function() {
                if( typeof(window.Plotly) !== "undefined" ){
                    MathJax.Hub.Config({ SVG: { font: "STIX-Web" }, displayAlign: "center" });
                    MathJax.Hub.Queue(["setRenderer", MathJax.Hub, "SVG"]);
                    clearInterval(waitForPlotly);
                }}, 250 );
        </script>
        """
    )
    init_notebook_mode(connected=True)
from colorlover import interp as color_interpolate
from plotly import tools
import plotly.graph_objs as go
import colorlover as cl
import math
import plotly.io as pio
pio.templates.default = "none"
import plotly.colors
from plotly.subplots import make_subplots
import pickle

colors = {'blues':['rgb(164,199,228)','rgb(119,171,214)','rgb(73,143,201)','rgb(49,113,165)','rgb(36,82,120)','rgb(23,52,76)'],
          'greens':['rgb(172,220,173)','rgb(130,203,133)','rgb(89,185,92)','rgb(63,152,66)','rgb(46,110,48)','rgb(28,67,29)'],
         'reds':['rgb(230,174,176)','rgb(218,133,137)','rgb(205,92,98)','rgb(187,57,64)','rgb(146,45,50)','rgb(104,32,35)'],
          #['rgb'+str(color) for color in plotly.colors.n_colors((254,224,210), (165,15,21), 6)],
         'pinks':['rgb(215,181,210)','rgb(195,144,188)','rgb(175,107,165)','rgb(147,79,137)','rgb(110,59,102)','rgb(74,40,69)'],
         'browns':['rgb(216,197,184)','rgb(196,168,148)','rgb(176,139,112)','rgb(150,111,83)','rgb(115,85,63)','rgb(80, 59, 44)'],
         'oranges': ['rgb(255,206,146)','rgb(255,189,109)','rgb(255,173,73)','rgb(255,157,36)','rgb(255, 140, 0)','rgb(219,120,0)'],
          'cyans': ['rgb(177,222,219)','rgb(139,205,201)','rgb(100,189,183)','rgb(70,163,157)','rgb(53,124,120)','rgb(37,87,84)'],
          'yellows': ['rgb(244,239,186)','rgb(239,231,151)','rgb(233,224,116)','rgb(228,216,82)','rgb(223,208,47)','rgb(200,185,31)',],
         'blacks':['rgb(182,182,182)','rgb(146,146,146)','rgb(109,109,109)','rgb(73,73,73)','rgb(36,36,36)','rgb(0,0,0)']}

colors_bg =  {'blues':['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['blues']],
              'greens':['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['greens']],
              'reds':['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['reds']],
              'pinks':['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['pinks']],
              'browns':['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['browns']],
              'oranges':['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['oranges']],
              'cyans': ['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['cyans']],
              'yellows': ['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['yellows']],
              'blacks':['rgba'+color.rstrip(')').lstrip('rgb')+',0.25)' for color in colors['blacks']]}
import numpy as np
import pandas as pd
from lmfit import Model
import plotly.io as pio
from openpyxl import load_workbook
from scipy.optimize import curve_fit
import plotly as py


with open('C:/Users/User/OneDrive - University of Toronto/Research/PhD_UofT/Data/Toggle_Switch_Project/Experiments/Screening/Autofluorescence_Models/gfp_models.pickle', 'rb') as handle:
    gfp_autofl_models = pickle.load(handle)

C:\Users\User\anaconda3\envs\impact\lib\site-packages\IPython\html.py:14: ShimWarning: The `IPython.html` package has been deprecated since IPython 4.0. You should import from `notebook` instead. `IPython.html.widgets` has moved to `ipywidgets`.
  "`IPython.html.widgets` has moved to `ipywidgets`.", ShimWarning)


In [3]:
def Hill(C, V_max, K_m, n):
    
    return V_max * C**n/(K_m**n + C**n)

def MicMenten(C, V_max, K_m, n):
    
    return V_max * C**2/(K_m**2 + C**2)


def fit_params(x, y, y_errs, V_max_init, K_m_init, n_init, func):

    params_dict = {'average':{},
                   'stdev':{}}

    params,cov = curve_fit(f=func, xdata=x, ydata=y,
                           p0=[V_max_init, K_m_init, n_init], sigma=y_errs, method='lm', absolute_sigma=True,# bounds=([0, 0, 1], [2*max(y), max(x), 8]),
                          maxfev=100000)
    params_std = np.sqrt(np.diag(cov))

    params_dict['average']['V_max'],\
    params_dict['average']['K_m'],\
    params_dict['average']['n']= params

    params_dict['stdev']['V_max'],\
    params_dict['stdev']['K_m'],\
    params_dict['stdev']['n']= params_std
    
    return params_dict

In [4]:
data_format='tecan_OD_GFP_mCherry'
plate_type = '96 Wells'
file_name = '20210613_FusTet_Tests_Kinetic.xlsx'
OD_data = parser.parse_raw_data(data_format=data_format,file_name=file_name,plate_type=plate_type)
expt_tet = OD_data
expt_tet.calculate()

gfp_models = [gfp_autofl_models['nofilm_inf'][110],gfp_autofl_models['nofilm_inf'][100], gfp_autofl_models['nofilm_inf'][90]]
for replicate in expt_tet.replicate_trials:
    if replicate.trial_identifier.strain.name.lower() != 'blank':
        for single_trial in replicate.single_trials:
            single_trial.analyte_dict['GFP'].pd_series.update(single_trial.analyte_dict['GFP'].pd_series - 
                                                              np.array([gfp_model(od_value) for (gfp_model, od_value) in zip(gfp_models, single_trial.analyte_dict['OD700'].pd_series.values)]))
            
expt_tet.calculate()



Importing data from 20210613_FusTet_Tests_Kinetic.xlsx...0.0s
Extracting timepoint data...Extracted time point data in 0.5s
Parsing time point list...Parsed 855 time points in 0.2s
Parsing analyte list...Parsed 95 single trials in 1001.5ms
Parsing single trial list...Parsed 40 replicates in 0.1s
Analyzing data...Ran analysis in 0.9s

Analyzing data...Ran analysis in 1.1s



In [5]:
data_format='tecan_OD_GFP_mCherry'
plate_type = '96 Wells'
file_name = '20210613_FusLac_Tests_Kinetic.xlsx'

OD_data = parser.parse_raw_data(data_format=data_format,file_name=file_name,plate_type=plate_type)
expt_lac = OD_data
expt_lac.calculate()

gfp_models = [gfp_autofl_models['nofilm_inf'][110],gfp_autofl_models['nofilm_inf'][100], gfp_autofl_models['nofilm_inf'][90]]
for replicate in expt_lac.replicate_trials:
    if replicate.trial_identifier.strain.name.lower() != 'blank':
        for single_trial in replicate.single_trials:
            single_trial.analyte_dict['GFP'].pd_series.update(single_trial.analyte_dict['GFP'].pd_series - 
                                                              np.array([gfp_model(od_value) for (gfp_model, od_value) in zip(gfp_models, single_trial.analyte_dict['OD700'].pd_series.values)]))
            
expt_lac.calculate()


Importing data from 20210613_FusLac_Tests_Kinetic.xlsx...0.1s
Extracting timepoint data...Extracted time point data in 0.7s
Parsing time point list...Parsed 855 time points in 0.4s
Parsing analyte list...Parsed 95 single trials in 1623.5ms
Parsing single trial list...Parsed 40 replicates in 0.2s
Analyzing data...Ran analysis in 1.1s

Analyzing data...Ran analysis in 1.4s



In [6]:
import colorlover as cl
from IPython.display import HTML
display(HTML(cl.to_html(py.colors.sequential.RdBu[0:5][::-1])))

In [7]:
sel_colors = colors['greens'][:-1]
inducer = 'atc'
units='ng/mL'
time_point = 1
concs = [0, 25, 50, 100, 250, 500, 1000, 2500]
strain_order = ['FusTestTet', 'FusTest1', 'FusTest2']
color_scale=["rgba(209, 235, 198, 1)",
              "rgba(133, 218, 97, 1)",
              "rgba(43, 132, 5, 1)"]


for analyte in ['GFP']:
    trace_list=[]
    for i,conc in enumerate(concs):
        if i!=0:
            color_index = (np.log10(conc) - np.log10(min(concs[1:])))/ (np.log10(max(concs[1:]))- np.log10(min(concs[1:]))) * (len(color_scale)-1)
            if np.isnan(color_index):
                color_index = 0
            lower_index = int(color_index)
            upper_index = lower_index + 1
            if lower_index >= (len(color_scale) - 1):
                color = color_scale[-1]
            elif upper_index < 1:
                color = color_scale[0]
            else:
                color = py.colors.find_intermediate_color(color_scale[lower_index], color_scale[upper_index], color_index - int(color_index), colortype='rgb')
        reps = [rep for rep in expt_tet.replicate_trials if rep.trial_identifier.media.components.get(inducer).concentration==conc and rep.trial_identifier.strain.name not in ['blank']]
        reps = [[rep for rep in reps if rep.trial_identifier.strain.name==strain][0] for strain in strain_order]

        x = [rep.trial_identifier.strain.name for rep in reps]
        if analyte!='OD700':
            od_value_0 = [rep.avg.analyte_dict['OD700'].data_vector[0] for rep in reps]
            od_value_1 = [rep.avg.analyte_dict['OD700'].data_vector[time_point] for rep in reps]
            y = [(rep.avg.analyte_dict[analyte].od_normalized_data[time_point]) for i, rep in enumerate(reps)]
            y_errs = [rep.std.analyte_dict[analyte].od_normalized_data[time_point] for rep in reps]
        else:
            y = [rep.avg.analyte_dict[analyte].data_vector[time_point] for rep in reps]
            y_errs = [rep.std.analyte_dict[analyte].data_vector[time_point] for rep in reps]
        if i==0:
            trace_list.append(go.Bar(x=x,
                                     y=y,
                                     error_y=dict(type='data', array=y_errs, thickness=1.5, width=3, color='black'),
                                     marker=dict(color=colors['blacks'][2],
                                     line=dict(width=0),
                                     colorbar=dict(title="Inducer Concentration (ng/mL)", thickness=13,len=1, title_side='right',
                                                   title_font=dict(family='Myriad Pro', size=20, color='black'),
                                                   tickfont=dict(family='Myriad Pro', size=20, color='black'), ticks='outside',
                                                   ticklen=5, tickwidth=1.5,dtick=1, x=1,ticktext=np.array([25,50,100,250,500,1000,2500]), tickvals=np.log10(concs[1:])),cmin=np.log10(min(concs[1:])), cmax=np.log10(max(concs[1:])),
                                     colorscale=color_scale),
                                     showlegend=True,# yaxis='y2',
                                     legendgroup=conc,
                                     name=str(conc)+' '+units))
        else:
            trace_list.append(go.Bar(x=x,
                         y=y,
                         error_y=dict(type='data', array=y_errs, thickness=1.5, width=3, color='black'),
                         marker=dict(color=color, #colorscale='RdBu',#([colors['blacks'][2]]+temp_colors)[i],
                         line=dict(width=0)),
                         showlegend=True,# yaxis='y2',
                         legendgroup=conc,
                         name=str(conc)+' '+units)) 
    fig=go.Figure(data=trace_list)
    fig.update_xaxes(showline=True, linewidth=1.25, linecolor='black', mirror=True, side='bottom',
                      ticks='outside', ticklen=8, tickangle=0, tickson='boundaries',
                      tickfont=dict(size=20, family='Myriad Pro', color='black'), tickcolor='black',
                      showgrid=False,zeroline=False)
    fig.update_layout(height=400, width=650, legend_orientation='h', legend_y=-0.1, showlegend=False,
                       title_font=dict(family='Myriad Pro',size=12, color='black'),
                       legend_x=-0.05, bargap=0.3, bargroupgap=0.1, title=analyte, title_y=.83, title_x=0.14,
                       legend_font=dict(family='Myriad Pro', size=14, color='black'))
    fig['layout']['title']['font'] = dict(family='Myriad Pro',size=16, color='black')
    fig['layout']['yaxis'] = dict(title='Fluorescence/OD700 (a.u.)', title_standoff=0,
                                 title_font=dict(family='Myriad Pro', size=20, color='black'),
                                 showline=True, linewidth=1.25, linecolor='black', mirror=True, nticks=7,
                                 ticks='outside', ticklen=6, tickangle=0, type='linear', range=(-1000,50000),
                                 tickfont=dict(family='Myriad Pro',size=20, color='black'), tickcolor='black', 
                                 showgrid=True,zeroline=False,side='left')
    plot(fig)
    fig.write_image('gfplaci_bars.svg', format='svg')

In [8]:
fig = make_subplots(rows=1, cols=3, horizontal_spacing=0.07)
trace_list=[]
for i, strain in enumerate(strain_order):
    reps = [rep for rep in expt_tet.replicate_trials if rep.trial_identifier.strain.name==strain]
    reps = sorted(reps, key=lambda rep: rep.trial_identifier.media.components['atc'].concentration)
    concs = [rep.trial_identifier.media.components['atc'].concentration for rep in reps]

    y = [rep.avg.analyte_dict[analyte].od_normalized_data[time_point] for i, rep in enumerate(reps)]
    y_errs = [rep.std.analyte_dict[analyte].od_normalized_data[time_point] for rep in reps]
    
    y = [value - y[0] for value in y]
    y_errs = [np.sqrt(value**2 + y_errs[0]**2) for value in y_errs]
    y = [value if value>0 else 0 for value in y]
    y_errs = [value if value>0 else 0 for value in y_errs]

    

    
    mm_params = fit_params(concs, y, y_errs, 10, 1000, 2, Hill)
    print(mm_params)
    fit_data = Hill(np.arange(0,1.5*concs[-1],1), mm_params['average']['V_max'],
                                            mm_params['average']['K_m'], mm_params['average']['n'])

    pos_n_fit_plus = Hill(np.arange(0,1.5*concs[-1],1), mm_params['average']['V_max']+mm_params['stdev']['V_max'],
                                                mm_params['average']['K_m']-mm_params['stdev']['K_m'],
                                                mm_params['average']['n']+mm_params['stdev']['n'])
    
    neg_n_fit_plus = Hill(np.arange(0,1.5*concs[-1],1), mm_params['average']['V_max']+mm_params['stdev']['V_max'],
                                                mm_params['average']['K_m']-mm_params['stdev']['K_m'],
                                                mm_params['average']['n']-mm_params['stdev']['n'])
    fit_plus = [max(neg_data, pos_data) for (neg_data,pos_data) in zip(neg_n_fit_plus, pos_n_fit_plus)]

    
    pos_n_fit_minus = Hill(np.arange(0,1.5*concs[-1],1), mm_params['average']['V_max']-mm_params['stdev']['V_max'],
                                            mm_params['average']['K_m']+mm_params['stdev']['K_m'],
                                            mm_params['average']['n']+mm_params['stdev']['n'])
    
    neg_n_fit_minus = Hill(np.arange(0,1.5*concs[-1],1), mm_params['average']['V_max']-mm_params['stdev']['V_max'],
                                                mm_params['average']['K_m']+mm_params['stdev']['K_m'],
                                                mm_params['average']['n']-mm_params['stdev']['n'])
    fit_minus = [min(neg_data, pos_data) for (neg_data,pos_data) in zip(neg_n_fit_minus, pos_n_fit_minus)]
    
    fig.add_trace(go.Scatter(x=np.arange(0,1.5*concs[-1],1),y=fit_data, 
                             name='Michaelis-Menten Fit',line={'width': 3,'color': colors['greens'][3]}, 
                             mode='lines', showlegend=False), row=1, col=i+1)
    
    fig.add_trace(go.Scatter(x=list(np.arange(0,1.5*concs[-1],1))+list(np.arange(0,1.5*concs[-1],1)[::-1]),
                         y=list(fit_plus) + list(fit_minus)[::-1],
                         mode='lines',
                         line={'color':'rgba(0,0,0,0)', 'shape':'spline'},
                         fill='toself',
                         fillcolor=colors_bg['greens'][3],
                         showlegend=False,
                         name="error"), row=1, col=i+1)
    
    fig.add_trace(go.Scatter(x=concs[1:], y=y[1:], error_y=dict(type='data', 
                                                                          array=y_errs[1:], thickness=1, 
                                                                          width=2, color='black'),
                            marker=dict(color=np.log10(concs[1:]), colorscale=["rgba(209, 235, 198, 1)",
              "rgba(133, 218, 97, 1)",
              "rgba(43, 132, 5, 1)"], size=10), mode='markers'), 
                  row=1, col=i+1)
fig.update_layout(height=400, width=900, showlegend=False)
fig.update_xaxes(showline=True, linewidth=1.25, linecolor='black', mirror=True, side='bottom',
                 title='Inducer Concentration (ng/mL)', 
                 title_font=dict(family='Myriad Pro', size=20, color='black'),
                title_standoff=50,
                 range=(np.log10(12.5),np.log10(3000)), type='log', tickvals=[25,50,100,250,500,1000,2500],
                  tickfont=dict(size=20, family='Myriad Pro', color='black'), tickcolor='black',
                  ticks='outside', ticklen=6, tickangle=90, tickson='boundaries',

                  showgrid=True,zeroline=False)


fig.update_yaxes(showline=True, linewidth=1.25, linecolor='black', mirror=True, side='bottom',
                  ticks='outside', ticklen=6, tickangle=0, tickson='boundaries',
                  tickfont=dict(size=20, family='Myriad Pro', color='black'), tickcolor='black', range=(0,45000),
                  showgrid=True,zeroline=False)
fig.update_yaxes(title='\u0394(Fluorescence/OD700) (a.u.)', title_standoff=0,
                                 title_font=dict(family='Myriad Pro', size=20, color='black'), row=1, col=1)

plot(fig)
fig.write_image('gfplaci_fit.svg', format='svg')

C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

divide by zero encountered in power

C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

invalid value encountered in double_scalars

C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

invalid value encountered in true_divide



{'average': {'V_max': 39768.12826589364, 'K_m': 105.63256921050773, 'n': 3.972409285792696}, 'stdev': {'V_max': 186.25873709803741, 'K_m': 0.7159603012054241, 'n': 0.11343851959174478}}
{'average': {'V_max': 33778.40107763549, 'K_m': 338.0341171685999, 'n': 2.923509745081046}, 'stdev': {'V_max': 227.55726031781896, 'K_m': 6.32593532465866, 'n': 0.12797470935089736}}


C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

overflow encountered in power



{'average': {'V_max': 26305.953028146563, 'K_m': 1545.3885548661258, 'n': 2.599195197556618}, 'stdev': {'V_max': 1711.771544962487, 'K_m': 77.02437900737891, 'n': 0.10925768808019855}}


In [9]:
inducer = 'IPTG'
width=600
units='mM'
time_point = 1
concs = [0, 0.025, 0.05, 0.1, 0.25, .5, 1, 2.5]
strain_order = ['FusTestLac', 'FusTest3', 'FusTest4']
color_scale=py.colors.sequential.RdBu[1:4][::-1]

for analyte in ['mCherry']:
    trace_list=[]
    for i,conc in enumerate(concs):
        if i!=0:
            color_index = (np.log10(conc) - np.log10(min(concs[1:])))/ (np.log10(max(concs[1:]))- np.log10(min(concs[1:]))) * (len(color_scale)-1)
            if np.isnan(color_index):
                color_index = 0
            lower_index = int(color_index)
            upper_index = lower_index + 1
            if lower_index >= (len(color_scale) - 1):
                color = color_scale[-1]
            elif upper_index < 1:
                color = color_scale[0]
            else:
                color = py.colors.find_intermediate_color(color_scale[lower_index], color_scale[upper_index], color_index - int(color_index), colortype='rgb')
        reps = [rep for rep in expt_lac.replicate_trials if rep.trial_identifier.media.components.get(inducer).concentration==conc and rep.trial_identifier.strain.name not in ['blank']]
        reps = [[rep for rep in reps if rep.trial_identifier.strain.name==strain][0] for strain in strain_order]

        x = [rep.trial_identifier.strain.name for rep in reps]
        if analyte!='OD700':
            y = [rep.avg.analyte_dict[analyte].od_normalized_data[time_point] for rep in reps]
            y_errs = [np.sqrt(rep.std.analyte_dict[analyte].od_normalized_data[time_point]**2) for rep in reps]
        else:
            y = [rep.avg.analyte_dict[analyte].data_vector[time_point] for rep in reps]
            y_errs = [rep.std.analyte_dict[analyte].data_vector[time_point] for rep in reps]
        temp_colors = color_interpolate(sel_colors, 7)
        if i==0:
            trace_list.append(go.Bar(x=x,
                                     y=y,
                                     error_y=dict(type='data', array=y_errs, thickness=1.5, width=3, color='black'),
                                     marker=dict(color=colors['blacks'][2],
                                     line=dict(width=0),
                                     colorbar=dict(title="Inducer Concentration (uM)", thickness=13,len=1, title_side='right',
                                                   title_font=dict(family='Myriad Pro', size=20, color='black'),
                                                   tickfont=dict(family='Myriad Pro', size=20, color='black'), ticks='outside',
                                                   ticklen=5, tickwidth=1.5,dtick=1, x=1,ticktext=np.array([25,50,100,250,500,1000,2500]), tickvals=np.log10(concs[1:])),cmin=np.log10(min(concs[1:])), cmax=np.log10(max(concs[1:])),
                                     colorscale=color_scale),
                                     showlegend=True,# yaxis='y2',
                                     legendgroup=conc,
                                     name=str(conc)+' '+units))
        else:
            trace_list.append(go.Bar(x=x,
                         y=y,
                         error_y=dict(type='data', array=y_errs, thickness=1.5, width=3, color='black'),
                         marker=dict(color=color,# colorscale='RdBu',#([colors['blacks'][2]]+temp_colors)[i],
                         line=dict(width=0)),
                         showlegend=True,# yaxis='y2',
                         legendgroup=conc,
                         name=str(conc)+' '+units)) 

    fig=go.Figure(data=trace_list)

    fig.update_xaxes(showline=True, linewidth=1.25, linecolor='black', mirror=True, side='bottom',
                  ticks='outside', ticklen=8, tickangle=0, tickson='boundaries',
                  tickfont=dict(size=20, family='Myriad Pro', color='black'), tickcolor='black',
                  showgrid=False,zeroline=False)
    fig.update_layout(height=400, width=650, legend_orientation='h', legend_y=-0.1, showlegend=False,
                       title_font=dict(family='Myriad Pro',size=12, color='black'),
                       legend_x=-0.05, bargap=0.3, bargroupgap=0.1, title=analyte, title_y=.83, title_x=0.14,
                       legend_font=dict(family='Myriad Pro', size=14, color='black'))
    fig['layout']['title']['font'] = dict(family='Myriad Pro',size=16, color='black')
    fig['layout']['yaxis'] = dict(title='Fluorescence/OD700 (a.u.)', title_standoff=0,
                                 title_font=dict(family='Myriad Pro', size=20, color='black'),
                                 showline=True, linewidth=1.25, linecolor='black', mirror=True, nticks=7,
                                 ticks='outside', ticklen=6, tickangle=0, type='linear', range=(0,40000),
                                 tickfont=dict(family='Myriad Pro',size=20, color='black'), tickcolor='black', 
                                 showgrid=True,zeroline=False,side='left')
    plot(fig)
    fig.write_image('tetrmche_bars.svg', format='svg')

In [10]:
py.colo

AttributeError: module 'plotly' has no attribute 'colo'

In [11]:
fig = make_subplots(rows=1, cols=3)
strain_order = ['FusTestLac', 'FusTest3', 'FusTest4']
concs=[0, 0.025, 0.05, 0.1, 0.25, .5, 1, 2.5]
trace_list=[]
for i, strain in enumerate(strain_order[:]):
    reps = [rep for rep in expt_lac.replicate_trials if rep.trial_identifier.strain.name==strain]
    reps = sorted(reps, key=lambda rep: rep.trial_identifier.media.components['IPTG'].concentration)
    concs = [rep.trial_identifier.media.components['IPTG'].concentration for rep in reps]

    y = [rep.avg.analyte_dict[analyte].od_normalized_data[time_point] for i, rep in enumerate(reps)]
    y_errs = [rep.std.analyte_dict[analyte].od_normalized_data[time_point] for rep in reps]
    y = [value - y[0] for value in y]
    y_errs = [np.sqrt(value**2 + y_errs[0]**2) for value in y_errs]
    
    y = [value if value>0 else 0 for value in y]
    y_errs = [value if value>0 else 0 for value in y_errs]

    mm_params = fit_params(concs, y, y_errs, 20000, 0.001, 1, Hill)
    print(mm_params)
    fit_data = Hill(np.arange(0,1.5*concs[-1],.001), mm_params['average']['V_max'],
                                            mm_params['average']['K_m'], mm_params['average']['n'])

    pos_n_fit_plus = Hill(np.arange(0,1.5*concs[-1],.001), mm_params['average']['V_max']+mm_params['stdev']['V_max'],
                                                mm_params['average']['K_m']-mm_params['stdev']['K_m'],
                                                mm_params['average']['n']+mm_params['stdev']['n'])
    
    neg_n_fit_plus = Hill(np.arange(0,1.5*concs[-1],.001), mm_params['average']['V_max']+mm_params['stdev']['V_max'],
                                                mm_params['average']['K_m']-mm_params['stdev']['K_m'],
                                                mm_params['average']['n']-mm_params['stdev']['n'])
    fit_plus = [max(neg_data, pos_data) for (neg_data,pos_data) in zip(neg_n_fit_plus, pos_n_fit_plus)]

    
    pos_n_fit_minus = Hill(np.arange(0,1.5*concs[-1],.001), mm_params['average']['V_max']-mm_params['stdev']['V_max'],
                                            mm_params['average']['K_m']+mm_params['stdev']['K_m'],
                                            mm_params['average']['n']+mm_params['stdev']['n'])
    
    neg_n_fit_minus = Hill(np.arange(0,1.5*concs[-1],.001), mm_params['average']['V_max']-mm_params['stdev']['V_max'],
                                                mm_params['average']['K_m']+mm_params['stdev']['K_m'],
                                                mm_params['average']['n']-mm_params['stdev']['n'])
    fit_minus = [min(neg_data, pos_data) for (neg_data,pos_data) in zip(neg_n_fit_minus, pos_n_fit_minus)]
    
    fig.add_trace(go.Scatter(x=np.arange(0,1.5*concs[-1],.001),y=fit_data, name='Michaelis-Menten Fit',line={'width': 3,'color': colors['reds'][3]}, mode='lines', showlegend=False), row=1, col=i+1)
    
    fig.add_trace(go.Scatter(x=list(np.arange(0,1.5*concs[-1],.001))+list(np.arange(0,1.5*concs[-1],.001)[::-1]),
                         y=list(fit_plus) + list(fit_minus)[::-1],
                         mode='lines',
                         line={'color':'rgba(0,0,0,0)', 'shape':'spline'},
                         fill='toself',
                         fillcolor=colors_bg['reds'][3],
                         showlegend=False,
                         name="error"), row=1, col=i+1)
    
    fig.add_trace(go.Scatter(x=concs[1:], y=y[1:], error_y=dict(type='data', 
                                                                          array=y_errs[1:], thickness=1, 
                                                                          width=2, color='black'),
                            marker=dict(color=np.log10(concs[1:]), colorscale=py.colors.sequential.RdBu[1:4][::-1],
                                        size=10), mode='markers'), 
                  row=1, col=i+1)
fig.update_layout(height=400, width=900, showlegend=False)
fig.update_xaxes(showline=True, linewidth=1.25, linecolor='black', mirror=True, side='bottom',
                 title='Inducer Concentration (uM)', 
                 title_font=dict(family='Myriad Pro', size=20, color='black'),
                title_standoff=50,
                 range=(np.log10(0.0125),np.log10(3.000)), type='log', tickvals=[.025,.050,.100,.250,.500,1.000,2.500], ticktext=[25, 50, 100, 250, 500, 1000, 2500],
                  tickfont=dict(size=20, family='Myriad Pro', color='black'), tickcolor='black',
                  ticks='outside', ticklen=6, tickangle=90, tickson='boundaries',

                  showgrid=True,zeroline=False)


fig.update_yaxes(showline=True, linewidth=1.25, linecolor='black', mirror=True, side='bottom',
                  ticks='outside', ticklen=6, tickangle=0, tickson='boundaries',
                  tickfont=dict(size=20, family='Myriad Pro', color='black'), tickcolor='black', range=(0,45000),
                  showgrid=True,zeroline=False)
fig.update_yaxes(title='\u0394(Fluorescence/OD700) (a.u.)', title_standoff=0,
                                 title_font=dict(family='Myriad Pro', size=20, color='black'), row=1, col=1)

plot(fig)
    
fig.write_image('tetrmche_fit.svg', format='svg')

{'average': {'V_max': 26053.262828590985, 'K_m': 0.020875241291151113, 'n': 22.44907646689414}, 'stdev': {'V_max': 329.1749575509187, 'K_m': 2385.036929956557, 'n': 13897663.071556643}}
{'average': {'V_max': 25236.341951415976, 'K_m': 0.007754496456391381, 'n': 1.250950264772551}, 'stdev': {'V_max': 413.5606536512449, 'K_m': 0.004514959640588872, 'n': 0.44862002873311135}}
{'average': {'V_max': 26795.26359523432, 'K_m': 0.0079664052824903, 'n': 2.0269915369219906}, 'stdev': {'V_max': 156.87891565010713, 'K_m': 0.004682439110584837, 'n': 1.0401697732865838}}


C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

overflow encountered in power

C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

invalid value encountered in double_scalars

C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

divide by zero encountered in power

C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

overflow encountered in double_scalars

C:\Users\User\anaconda3\envs\impact\lib\site-packages\ipykernel_launcher.py:3: RuntimeWarning:

invalid value encountered in true_divide

